# 提示词工程
## 视频地址：https://www.bilibili.com/video/BV1173jzNELG/

- 视频来源：DeepLearning.AI
- ①学习提示工程最好的应用开发实践
- ②探索使用LLM的新方法，包括如何构建自己的自定义聊天机器人
- ③使用OpenAI API上手练习编写和迭代提示词


## API
本笔记使用 openrouter/aliyun 的免费 api替代 openai api。如使用 openai，调整 model name即可

In [1]:
# key
# api_keys: str = "sk-or-v1-" # openrouter
api_keys: str = "sk-" # ali

# name
#model_name: str = "qwen/qwen3-235b-a22b:free"
model_name: str = "qwen3-235b-a22b-thinking-2507"

#base url
# base_url: str = "https://openrouter.ai/api/v1"
base_url: str = "https://dashscope.aliyuncs.com/compatible-mode/v1"

In [2]:
# check openrouter rate limit
import requests
import json

limit_info = lambda apikeys: json.dumps(requests.get(url=f"{base_url}/key",
                                                     headers={"Authorization": f"Bearer {apikeys}"}
                                                    ).json(),
                                        indent=2,
                                       )
if base_url == "https://openrouter.ai/api/v1":
    print(limit_info(api_keys))

In [3]:
#wrapper to remove think tag
import re
from typing import Callable
from functools import wraps

def strip_think_tags(text: str) -> str:
    """
    ensure that there's no fucking <think> tag in the fucking response from model
    """
    pattern: str = r'<think>.*?</think>'
    return re.sub(pattern, '', text, flags=re.DOTALL)

def NO_THINKING(func: Callable) -> Callable:
    @wraps(func)
    def wrapped(*args, **kargs):
        return strip_think_tags(func(*args, **kargs))
    return wrapped


In [4]:
from openai import OpenAI

client = OpenAI(
      base_url=base_url,
      api_key=api_keys,
)

In [5]:
@NO_THINKING
def get_completion(prompt: str, model: str=model_name) -> str:
    messages = [{"role": "user", "content": prompt}]
    response = client.chat.completions.create(model=model, messages=messages, temperature=0)
    return response.choices[0].message.content


In [6]:
#test
y = get_completion("你好")

In [7]:
print(y)

你好！😊 很高兴见到你～有什么我可以帮忙的吗？无论是问题、闲聊，还是需要点小建议，我都在这儿哦！


# 1- Guide(模型引导)

In this lesson, we'll practice two prompting principles and their related tactics in order to write effective prompts for large language models.

## Principle 1
**Write clear and specific instructions (noted: clear != short)**

### Tactic 1: using delimiters like:
1. """，
2. \```，
3. ---，
4. <>
5. \<Example> example \</Example>
   
使用分隔符能让模型知道自己需要处理的准确内容，也可以**防止“prompt injection”**

In [8]:
text = f"""
You should express what you want a model to do by\
providing instructions that are as clear and\
specific as you can possibly make them.\
This will guide the model towards the desired output,\
and reduce the chances of receiving irrelevant\
or incorrect responses. Don't confuse writing a\
clear prompt with writing a short prompt.\
In many cases, longer prompts provide more clarity\
and context for the model, which can lead to\
more detailed and relevant outputs.\
"""

prompt = f"""
Summarize the text delimited by triple backticks
into a single sentence.
```{text}```
"""
response = get_completion(prompt)
print(response)

To guide AI models toward relevant outputs, provide clear, specific, and sufficiently detailed instructions—prioritizing clarity over brevity—as additional context reduces ambiguity and minimizes incorrect responses.


### Tactic 2: asking structured output
like json, html

In [9]:
prompt = f"""
Generate a list of 5 made-up book titles along
with their authors and genres.
Provide them in Json format with the following :
book_id, title, author, genre.
"""

response = get_completion(prompt)
print(response)



[
  {
    "book_id": 1,
    "title": "Whispers of the Chronos Forest",
    "author": "Elara Voss",
    "genre": "Fantasy"
  },
  {
    "book_id": 2,
    "title": "Neon Requiem in Sector 9",
    "author": "Jax Morrow",
    "genre": "Cyberpunk"
  },
  {
    "book_id": 3,
    "title": "The Alchemist's Last Equation",
    "author": "Dr. Thaddeus Finch",
    "genre": "Historical Mystery"
  },
  {
    "book_id": 4,
    "title": "Echoes from the Glass Desert",
    "author": "Sofia Raine",
    "genre": "Post-Apocalyptic"
  },
  {
    "book_id": 5,
    "title": "Lunar Tea Shop of Forgotten Memories",
    "author": "Ming Chen",
    "genre": "Magical Realism"
  }
]


### Tactic 3: checking whether conditions are satisfied

check assumptions required to the task


In [10]:
text_1 = f"""
Making a cup of tea is easy! First, you need to get some\
water boiling. While that's happening,\
grab a cup and put a tea bag in it. Once the water is\
hot enough, just pour it over the tea bag.\
Let it sit for a bit so the tea can steep. After a\
few minutes, take out the tea bag. If you\
like, you can add some sugar or milk to taste.\
And that's it! You've got yourself a delicious\
cup of tea to enjoy.
"""

prompt_1 = f"""
You will be provided with text delimited by triple quotes.\
If it contains a sequence of instructions,\
re-write those instructions in the following format:

Step 1:  ...
Step 2:  ...
...
Step N:  ...

If the text does not contain a sequence of instructions,
then simply write "No steps provided.\"

here is the text:
\"\"\"{text_1}\"\"\"
"""

response = get_completion(prompt_1)
print("Completion for Text 1:")
print(response)

Completion for Text 1:
Step 1: Get some water boiling.  
Step 2: Grab a cup and put a tea bag in it.  
Step 3: Pour the hot water over the tea bag.  
Step 4: Let the tea steep for a few minutes.  
Step 5: Take out the tea bag.  
Step 6: Add sugar or milk to taste, if desired.


In [11]:
text_2=f"""
The sun is shining brightly today, and the birds are
singing. It's a beautiful day to go for a
walk in the park. The flowers are blooming, and the
trees are swaying gently in the breeze. People
are out and about, enjoying the lovely weather.
Some are having picnics, while others are playing
l
games or simply relaxing on the grass. It's a
perfect day to spend time outdoors and appreciate the
beauty of nature.
"""

prompt_2 = f"""
You will be provided with text delimited by triple quotes.\
If it contains a sequence of instructions,\
re-write those instructions in the following format:

Step 1:  ...
Step 2:  ...
...
Step N:  ...

If the text does not contain a sequence of instructions,
then simply write "No steps provided.\"

here is the text:
\"\"\"{text_2}\"\"\"
"""

response = get_completion(prompt_2)
print("Completion for Text 2:")
print(response)

Completion for Text 2:
No steps provided.


### Tactic 4: few-shot prompting

give successful example of completing task, then ask the model to perform the task


In [12]:
prompt = f"""
Your task is to answer in a consistent style.

<child>: Teach me about patience.

<grandparent>: The river that carves the deepest\
valley flows from a modest spring; the\
grandest symphony originates from a single note;\
the most intricate tapestry begins with a solitary thread.

<child>: Teach me about resilience."""

response = get_completion(prompt)
print(response)

<child>: Teach me about resilience.  

<grandparent>: The strongest tree that stands unbroken after the storm rises from a seed cracked open by winter; the most supple bamboo that bends without breaking in the typhoon's rage grows from a shoot bent low by the first wind; the most luminous pottery repaired with golden seams emerges from a vessel shattered by the fall.


## Principle 2
**Give the model time to think**


In [13]:
text = f"""
In a charming village, siblings Jack and Jill set out on\
a quest to fetch water from a hilltop\
well. As they climbed, singing joyfully, misfortune\
struck-Jack tripped on a stone and tumbled\
down the hill, with Jill following suit.\
Though slightly battered, the pair returned home to\
comforting embraces. Despite the mishap,\
their adventurous spirits remained undimmed, and they\
continued exploring with delight.
"""

# example 1
prompt_3 = f"""
Perform the following actions:
1 - Summarize the following text delimited by xml tag \
<text></text> with 1 sentence.
2 - Translate the summary into French.
3 - List each name in the French summary.
4 - Output a json object that contains the following\
keys: original_summary, french_summary, num_names.

Separate your anywers with line breaks.

Text:
 <text> {text} </text>
"""
response = get_completion(prompt_3)
print("Completion for prompt 3:")
print(response)

Completion for prompt 3:
Siblings Jack and Jill tumbled down a hill while fetching water but returned home safely and continued their adventures.
Jack et Jill, frère et sœur, sont tombés de la colline en allant chercher de l'eau, mais sont rentrés chez eux sains et saufs et ont continué leurs aventures.
Jack, Jill
{"original_summary": "Siblings Jack and Jill tumbled down a hill while fetching water but returned home safely and continued their adventures.", "french_summary": "Jack et Jill, frère et sœur, sont tombés de la colline en allant chercher de l'eau, mais sont rentrés chez eux sains et saufs et ont continué leurs aventures.", "num_names": 2}


In [14]:
# example 2, asking for output in a specified format
text = f"""
In a charming village, siblings Jack and Jill set out on\
a quest to fetch water from a hilltop\
well. As they climbed, singing joyfully, misfortune\
struck-Jack tripped on a stone and tumbled\
down the hill, with Jill following suit.\
Though slightly battered, the pair returned home to\
comforting embraces. Despite the mishap,\
their adventurous spirits remained undimmed, and they\
continued exploring with delight.
"""

prompt_4 = f"""
Perform the following actions:
1 - Summarize the following text delimited by xml tag \
<text></text> with 1 sentence.
2 - Translate the summary into French.
3 - List each name in the French summary.
4 - Output a json object that contains the following\
keys: original_summary, french_summary, num_names.

you should use the following format to show your result:
Text: <text to summarize> \n
Summary: <summary> \n 
Translation: <summary translation> \n
Output JSON: <json with summary and num_names>

Text:
 <text> {text} </text>
"""
response = get_completion(prompt_4)
print("Completion for prompt 4:")
print(response)

Completion for prompt 4:
Text: In a charming village, siblings Jack and Jill set out on a quest to fetch water from a hilltop well. As they climbed, singing joyfully, misfortune struck—Jack tripped on a stone and tumbled down the hill, with Jill following suit. Though slightly battered, the pair returned home to comforting embraces. Despite the mishap, their adventurous spirits remained undimmed, and they continued exploring with delight. 

Summary: Siblings Jack and Jill ventured to fetch water from a hilltop well, suffered a fall during their climb, but returned home safely and continued exploring joyfully. 
 
Translation: Jack et Jill, frère et sœur, sont partis chercher de l'eau d'un puits en haut de la colline, sont tombés pendant leur ascension, mais sont rentrés chez eux sains et saufs et ont continué à explorer avec enthousiasme. 

Names in French summary: Jack, Jill

Output JSON: {"original_summary": "Siblings Jack and Jill ventured to fetch water from a hilltop well, suffered

In [15]:
prompt_5 = f"""
Your task is fo determine if the student's solution is correct or not.
To solve the problem do the following:
- First, work out your own solution to the problem.
- Then compare your solution to the student's solution and evaluate if the student's solution is correct or not.\
Don't decide if the student's solution is correct until you have done the problem yourself.

Use the following format:
Question:
```question here```

Student's solution:
```student's solution here```

Actual solution:
```steps to work out the solution and your solution here```

Is the student's solution the same as actual solution just calculated:
```yes or no``

Student grade:
```correct or incorrect```


Question:
```
I'm buildipg a solar power installation and I need help working ouf the financials.

- Land costs $1oo / square foot
- I can buy solar panels for $250 / square foot
- I negotiated a contract for maintenance that will cost \
me a flat $look per year, and an additional $10 / square foot

What is the total cost for the first year of operations as a function of the number of square feet.
```

Student's solution:
```
Let x be the size of the installation in square feet.
Costs:
1. Land cost: 100x
2. Solar panel cost: 250x
3. Maintenance cost: 100,000 + 100x
Total c0st:100x + 250x+ 100,000 + 100x = 450x+ 100,000
```
"""
response = get_completion(prompt_5)
print("Completion for prompt 5:")
print(response)


Completion for prompt 5:
Question:
```
I'm buildipg a solar power installation and I need help working ouf the financials.

- Land costs $1oo / square foot
- I can buy solar panels for $250 / square foot
- I negotiated a contract for maintenance that will cost me a flat $look per year, and an additional $10 / square foot

What is the total cost for the first year of operations as a function of the number of square feet.
```

Student's solution:
```
Let x be the size of the installation in square feet.
Costs:
1. Land cost: 100x
2. Solar panel cost: 250x
3. Maintenance cost: 100,000 + 100x
Total c0st:100x + 250x+ 100,000 + 100x = 450x+ 100,000
```

Actual solution:
```
Let x = number of square feet.

1. Land cost: $100/sq ft → 100x (correcting "$1oo" typo to $100)
2. Solar panel cost: $250/sq ft → 250x
3. Maintenance cost: Flat $100,000/year (correcting "$look" typo to $100,000) + $10/sq ft → 100,000 + 10x

Total cost = Land + Solar Panels + Maintenance
Total cost = 100x + 250x + (100,00

## Model Limitations
**Hallucination**

Make statements that sound plausible but are not true

**Reduce Hallucination**
First find relevant information then answer the question based on the relevant information

In [16]:
prompt = f"""
Tell me about AreoGlide UltraSlim Smart Toothbrush by Boie
"""
response = get_completion(prompt)
print("Completion for prompt 6:")
print(response)

Completion for prompt 6:
That's an interesting query, but **there is no such product as the "AreoGlide UltraSlim Smart Toothbrush by Boie."** This appears to be a **mix-up, misunderstanding, or potentially a scam/fake product listing.** Let me clarify why and provide accurate information:

### 1. **Boie Does NOT Make a "Smart" or "UltraSlim" Toothbrush**
   - **Boie** (the real company) is known for its **innovative, bristle-free, silicone toothbrush** (simply called the **Boie Toothbrush**). It's designed for gentle, hygienic cleaning using medical-grade silicone and a unique oscillating motion.
   - **Key features of the *real* Boie toothbrush:**
     - **Bristle-free design:** Uses soft silicone nubs instead of traditional bristles (reduces bacteria buildup).
     - **Body-safe materials:** Medical-grade silicone, no plastic bristles.
     - **Rechargeable:** Magnetic charging base (lasts ~2 weeks per charge).
     - **NOT "ultra-slim":** It has a **chunky, ergonomic handle** (about

# 2- Iterative Prompt Development(提示词敏捷开发)

**Iterative Process Loop**
<br>
- Try something
- Analyze where the result does not give what you want
- Clarify instructions, give more time to think
- Refine prompts with a batch of examples

It is saying that you are doing the following iteration:
- Be clear and specific
- Analyze why result does not give desired output
- Refine the idea and the prompt
- Repeat



## Example 1: Summarizing the information of an chair

You will see how to adjust/experiment the prompt to get the desired output from model step by step

### Issue 1: just summarize

In [17]:
fact_sheet_of_a_chair = """
OVERVIEW
- Part of a beautiful family of mid-century inspired office furniture, 
including filing cabinets, desks, bookcases, meeting tables, and more.
- Several options of shell color and base finishes.
- Available with plastic back and front upholstery (SWC-100) 
or full upholstery (SWC-110) in 10 fabric and 6 leather options.
- Base finish options are: stainless steel, matte black, 
gloss white, or chrome.
- Chair is available with or without armrests.
- Suitable for home or business settings.
- Qualified for contract use.

CONSTRUCTION
- 5-wheel plastic coated aluminum base.
- Pneumatic chair adjust for easy raise/lower action.

DIMENSIONS
- WIDTH 53 CM | 20.87”
- DEPTH 51 CM | 20.08”
- HEIGHT 80 CM | 31.50”
- SEAT HEIGHT 44 CM | 17.32”
- SEAT DEPTH 41 CM | 16.14”

OPTIONS
- Soft or hard-floor caster options.
- Two choices of seat foam densities: 
 medium (1.8 lb/ft3) or high (2.8 lb/ft3)
- Armless or 8 position PU armrests 

MATERIALS
SHELL BASE GLIDER
- Cast Aluminum with modified nylon PA6/PA66 coating.
- Shell thickness: 10 mm.
SEAT
- HD36 foam

COUNTRY OF ORIGIN
- Italy
"""

### Issue 2: summarize for consumers

In [18]:
# for consumers
prompt = f"""
Your task is to help a marketing team create a 
description for a retail website of a product based 
on a technical fact sheet.

Write a product description based on the information 
provided in the technical specifications delimited by 
triple backticks.

Technical specifications: ```{fact_sheet_of_a_chair}```
"""
response = get_completion(prompt)
print(response) # it is tooo long

## Elevate Your Space with Timeless Italian Design: The SWC Executive Chair  

Step into the legacy of mid-century modern elegance with the SWC Executive Chair—a masterpiece of Italian craftsmanship designed for those who refuse to compromise on style or substance. Born in the heart of Italy and refined for today’s dynamic workspaces, this chair isn’t just furniture; it’s a statement of sophistication for your home office, corporate suite, or creative studio.  

**Why Designers and Discerning Professionals Love the SWC:**  
✨ **Your Vision, Perfected:** Choose from 10 premium fabrics or 6 supple leathers to create *your* signature look. Pair it with a shell in any hue, a base in stainless steel, matte black, gloss white, or chrome, and decide: sleek armless minimalism or 8-position PU armrests for ultimate support. Whether you crave a pop of color or understated luxury, the SWC adapts to *your* aesthetic.  
✨ **Engineered for Effortless Comfort:** Sink into HD36 high-density foam (sele

### Issue 3 summary is too long, constraint it within 50 words

In [19]:
prompt = f"""
Your task is to help a marketing team create a 
description for a retail website of a product based 
on a technical fact sheet.

Write a product description based on the information 
provided in the technical specifications delimited by 
triple backticks.

use 50 words at most

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words.

Technical specifications: ```{fact_sheet_of_a_chair}```
"""
response = get_completion(prompt)
print(response) 

Elegant Italian mid-century office chair with multiple shell colors and fabric/leather upholstery options. Features smooth height adjustment, choice of armrests, and commercial-grade durability for home or office. Timeless design, contract-qualified.


In [20]:
len(response.split(" "))

30

### Issue 4 summarize for retailer

In [21]:
# for furniture retailers
prompt = f"""
Your task is to help a marketing team create a 
description for a retail website of a product based 
on a technical fact sheet.

Write a product description based on the information 
provided in the technical specifications delimited by 
triple backticks.

The description is intended for furniture retailers, 
so should be technical in nature and focus on the 
materials the product is constructed from.

use 50 words at most

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words.

Technical specifications: ```{fact_sheet_of_a_chair}```
"""
response = get_completion(prompt)
print(response)

Italian-crafted office chair features 10mm cast aluminum shell with PA6/PA66 nylon coating, plastic-coated aluminum 5-wheel base, and HD36 seat foam. Pneumatic height adjustment. Contract-qualified construction ensures commercial durability with precise material specifications for professional environments.


### Issue 5 attach more details to summary

In [22]:
# for furniture retailers and ID of furniture attached in the end of output
prompt = f"""
Your task is to help a marketing team create a 
description for a retail website of a product based 
on a technical fact sheet.

Write a product description based on the information 
provided in the technical specifications delimited by 
triple backticks.

The description is intended for furniture retailers, 
so should be technical in nature and focus on the 
materials the product is constructed from.

At the end of the description, include every 7-character 
Product ID in the technical specification, follow the rule:
ID:```the ID1 of furniture, the ID2 of furniture ... the IDn of furniture ```

use 50 words at most

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words. 

Technical specifications: ```{fact_sheet_of_a_chair}```
"""
response = get_completion(prompt)
print(response)

Mid-century office chair with cast aluminum base (PA6/PA66 coated), 10mm shell, HD36 foam seat. 5-wheel plastic-coated aluminum base. Options: SWC-100 (plastic upholstery) or SWC-110 (full upholstery). ID:SWC-100, SWC-110


### Issue 6 make summary into html for website

In [23]:
# for furniture retailers and ID of furniture attached in the end of output
prompt = f"""
Your task is to help a marketing team create a 
description for a retail website of a product based 
on a technical fact sheet.

Write a product description based on the information 
provided in the technical specifications delimited by 
triple backticks.

The description is intended for furniture retailers, 
so should be technical in nature and focus on the 
materials the product is constructed from.

At the end of the description, include every 7-character 
Product ID in the technical specification, follow the rule:
ID:```the ID1 of furniture, the ID2 of furniture ... the IDn of furniture ```

After the description, include a table that gives the 
product's dimensions. The table should have three columns.
In the first column include the name of the dimension. 
In the second column include the measurements in inches only.
In the thire column include the measurements in centimeters only.

Give the table the title 'Product Dimensions'.

Format everything as HTML that can be used in a website. 
Place the description in a <div> element.

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words.
you SHOULD remove <think></think> tag and the contents within from output. 
simply show the output.

Technical specifications: ```{fact_sheet_of_a_chair}```
"""
response = get_completion(prompt)
print(response)

<div>
<p>This mid-century inspired office chair, part of a comprehensive contract-grade furniture collection, features precision engineering and premium material specifications for commercial and residential applications. The shell base glider utilizes cast aluminum with a modified nylon PA6/PA66 coating for superior durability and 10 mm shell thickness, ensuring structural integrity under continuous use. The seat construction employs HD36 foam with optional density selections (1.8 lb/ft³ medium or 2.8 lb/ft³ high) to meet ergonomic requirements. Available in two primary configurations: SWC-100 with plastic back/front upholstery or SWC-110 with full upholstery, both supporting 10 fabric and 6 leather options. The 5-wheel plastic-coated aluminum base incorporates pneumatic height adjustment mechanisms and offers finish choices in stainless steel, matte black, gloss white, or chrome. Optional components include soft/hard-floor casters and 8-position PU armrests or armless configurations,

In [24]:
from IPython.display import display, HTML, Markdown

In [25]:
display(HTML(response))

# 3- Summarizing(摘要总结)

try to summarize text with a focus on specific topics.


In [26]:
prod_review = """
Got this panda plush toy for my daughter's birthday, \
who loves it and takes it everywhere. It's soft and \ 
super cute, and its face has a friendly look. It's \ 
a bit small for what I paid though. I think there \ 
might be other options that are bigger for the \ 
same price. It arrived a day earlier than expected, \ 
so I got to play with it myself before I gave it \ 
to her.
"""

### Task 1: general summary

In [27]:
prompt = f"""
Your task is to generate a short summary of a product \
review from an ecommerce site. 

Summarize the review below, delimited by triple 
backticks, in at most 30 words. 

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words.
you SHOULD remove <think></think> tag and the contents within from output. 
simply show the output.

Review: ```{prod_review}```
"""

response = get_completion(prompt)
print(response)

Daughter loves the soft, cute panda plush, but it's smaller than expected for the price. Arrived early, highly cherished.


### Task 2: Specific summary

In [28]:
prompt = f"""
Your task is to generate a short summary of a product \
review from an ecommerce site. 

Summarize the review below, delimited by triple 
backticks, in at most 30 words. and focus on any aspescts that are relevant to the price abd perceived value.

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words.
you SHOULD remove <think></think> tag and the contents within from output. 
simply show the output.

Review: ```{prod_review}```
"""

response = get_completion(prompt)
print(response)

Soft, cute panda plush loved by child, but perceived as too small for the price; reviewer suggests larger alternatives may offer better value at same cost.


### Task 3: Extract info from summary

In [29]:
prompt = f"""
Your task is to extract relevant information from \ 
a product review from an ecommerce site to give \
feedback to the Shipping department. 

From the review below, delimited by triple quotes \
extract the information relevant to shipping and \ 
delivery. Limit to 30 words. 

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words.
you SHOULD remove <think></think> tag and the contents within from output. 
simply show the output.

Review: ```{prod_review}```
"""

response = get_completion(prompt)
print(response)

Arrived a day earlier than expected.


### Task 4: Batch Summaries

In [30]:
review_1 = prod_review 

# review for a standing lamp
review_2 = """
Needed a nice lamp for my bedroom, and this one \
had additional storage and not too high of a price \
point. Got it fast - arrived in 2 days. The string \
to the lamp broke during the transit and the company \
happily sent over a new one. Came within a few days \
as well. It was easy to put together. Then I had a \
missing part, so I contacted their support and they \
very quickly got me the missing piece! Seems to me \
to be a great company that cares about their customers \
and products. 
"""

# review for an electric toothbrush
review_3 = """
My dental hygienist recommended an electric toothbrush, \
which is why I got this. The battery life seems to be \
pretty impressive so far. After initial charging and \
leaving the charger plugged in for the first week to \
condition the battery, I've unplugged the charger and \
been using it for twice daily brushing for the last \
3 weeks all on the same charge. But the toothbrush head \
is too small. I’ve seen baby toothbrushes bigger than \
this one. I wish the head was bigger with different \
length bristles to get between teeth better because \
this one doesn’t.  Overall if you can get this one \
around the $50 mark, it's a good deal. The manufactuer's \
replacements heads are pretty expensive, but you can \
get generic ones that're more reasonably priced. This \
toothbrush makes me feel like I've been to the dentist \
every day. My teeth feel sparkly clean! 
"""

# review for a blender
review_4 = """
So, they still had the 17 piece system on seasonal \
sale for around $49 in the month of November, about \
half off, but for some reason (call it price gouging) \
around the second week of December the prices all went \
up to about anywhere from between $70-$89 for the same \
system. And the 11 piece system went up around $10 or \
so in price also from the earlier sale price of $29. \
So it looks okay, but if you look at the base, the part \
where the blade locks into place doesn’t look as good \
as in previous editions from a few years ago, but I \
plan to be very gentle with it (example, I crush \
very hard items like beans, ice, rice, etc. in the \ 
blender first then pulverize them in the serving size \
I want in the blender then switch to the whipping \
blade for a finer flour, and use the cross cutting blade \
first when making smoothies, then use the flat blade \
if I need them finer/less pulpy). Special tip when making \
smoothies, finely cut and freeze the fruits and \
vegetables (if using spinach-lightly stew soften the \ 
spinach then freeze until ready for use-and if making \
sorbet, use a small to medium sized food processor) \ 
that you plan to use that way you can avoid adding so \
much ice if at all-when making your smoothie. \
After about a year, the motor was making a funny noise. \
I called customer service but the warranty expired \
already, so I had to buy another one. FYI: The overall \
quality has gone done in these types of products, so \
they are kind of counting on brand recognition and \
consumer loyalty to maintain sales. Got it in about \
two days.
"""

reviews = [review_1, review_2, review_3, review_4]

In [31]:
from time import sleep # openrouter api request rate limitation

base_prompt = """
Your task is to generate a short summary of a product \
review from an ecommerce site. 

Summarize the review below, delimited by triple 
backticks, in at most 20 words. 

Notice:
your output should NOT be quoted by any delimiters like \", \', ---, `, etc.., and no need to confirm the number of words.
you SHOULD remove <think></think> tag and the contents within from output. 
simply show the output.

Review: ```{}```
"""
for idx, review in enumerate(reviews, 1):
    review_prompt = base_prompt.format(review)
    # print(review_prompt)
    response = get_completion(review_prompt)
    print(idx, response, "\n")
    sleep(1) # openrouter api request rate limitation
    

1 Daughter loves soft, cute panda plush with friendly face, but size is small for price; arrived early. 

2 Affordable lamp with storage; fast delivery. Company quickly replaced broken string and missing part, showing excellent customer care. 

3 Hygienist-recommended with long battery life but small head and costly replacements; good value around $50. 

4 Price increased significantly; quality declined with motor failure after a year, warranty expired requiring repurchase. 



# 4- Inferring(模型推理)
hereby, we will try to infer sentiment and topics from product reviews and news articles.


In [32]:
lamp_review = """
Needed a nice lamp for my bedroom, and this one had \
additional storage and not too high of a price point. \
Got it fast.  The string to our lamp broke during the \
transit and the company happily sent over a new one. \
Came within a few days as well. It was easy to put \
together.  I had a missing part, so I contacted their \
support and they very quickly got me the missing piece! \
Lumina seems to me to be a great company that cares \
about their customers and products!!
"""

### base inferring

In [33]:
prompt = f"""
What is the sentiment of the following product review, 
which is delimited with triple backticks?

Review text: '''{lamp_review}'''
"""
response = get_completion(prompt)
print(response)

The sentiment of the product review is **positive**.  

### Key Reasons:  
1. **Overwhelmingly Positive Language**:  
   - The reviewer highlights multiple strengths: "additional storage," "not too high of a price point," "easy to put together," and praises the company as "great" that "cares about their customers and products!!" (note the enthusiastic double exclamation marks).  
   - Phrases like "happily sent," "very quickly got me the missing piece," and "cares about their customers" emphasize strong satisfaction.  

2. **Negative Events Resolved Positively**:  
   - While the review mentions issues (broken string during transit, missing part), these are framed as **resolved successfully** by the company. The focus is on the *excellent customer service* (e.g., "company happily sent over a new one," "support very quickly got me the missing piece"), turning potential negatives into positives.  

3. **Overall Tone and Conclusion**:  
   - The review starts and ends with praise (e.g., "

### Sentiment (positive/negative) (in specific format)

In [34]:
prompt = f"""
What is the sentiment of the following product review, 
which is delimited with triple backticks?

Give your answer as a single word, either "positive" \
or "negative".

Review text: '''{lamp_review}'''
"""
response = get_completion(prompt)
print(response)

positive


In [35]:
prompt = f"""
What is the sentiment of the following product review, 
which is delimited with triple backticks?

simply output in JSON format, include key sentiment

the value of key sentiment could be POSITIVE, NEUTRAL or NEGATIVE. Depends on your analysis.

Review text: '''{lamp_review}'''
"""
response = get_completion(prompt)
print(response)

{
  "sentiment": "POSITIVE"
}


### Identify types of emotions

In [36]:
prompt = f"""
Identify a list of emotions that the writer of the \
following review is expressing. Include no more than \
five items in the list. Format your answer as a python list of \
lower-case words items.

Review text: '''{lamp_review}'''
"""
response = get_completion(prompt)
print(response)

['satisfied', 'grateful', 'happy', 'impressed', 'pleased']


### Identify anger

In [37]:
prompt = f"""
Is the writer of the following review expressing anger?\
The review is delimited with triple backticks. \
Give your answer as either yes or no.

Review text: '''{lamp_review}'''
"""
response = get_completion(prompt)
print(response)

no


### Extract product and company name from customer reviews


In [38]:
prompt = f"""
Identify the following items from the review text: 
- Item purchased by reviewer
- Company that made the item

The review is delimited with triple backticks. \
Format your response as a JSON object with \
"Item" and "Brand" as the keys. 
If the information isn't present, use "unknown" \
as the value.
Make your response as short as possible.
  
Review text: '''{lamp_review}'''
"""
response = get_completion(prompt)
print(response)

{"Item": "lamp", "Brand": "Lumina"}


### Doing multiple task in one prompt

In [39]:
prompt = f"""
Identify the following items from the review text: 
- Sentiment (positive or negative)
- Is the reviewer expressing anger? (true or false)
- Item purchased by reviewer
- Company that made the item

The review is delimited with triple backticks. \
Format your response as a JSON object with \
"Sentiment", "Anger", "Item" and "Brand" as the keys.
If the information isn't present, use "unknown" \
as the value.
Make your response as short as possible.
Format the Anger value as a boolean.

Review text: '''{lamp_review}'''
"""
response = get_completion(prompt)
print(response)

{"Sentiment":"positive","Anger":false,"Item":"lamp","Brand":"Lumina"}


### Inferring topics

In [40]:
story = """
In a recent survey conducted by the government, 
public sector employees were asked to rate their level 
of satisfaction with the department they work at. 
The results revealed that NASA was the most popular 
department with a satisfaction rating of 95%.

One NASA employee, John Smith, commented on the findings, 
stating, "I'm not surprised that NASA came out on top. 
It's a great place to work with amazing people and 
incredible opportunities. I'm proud to be a part of 
such an innovative organization."

The results were also welcomed by NASA's management team, 
with Director Tom Johnson stating, "We are thrilled to 
hear that our employees are satisfied with their work at NASA. 
We have a talented and dedicated team who work tirelessly 
to achieve our goals, and it's fantastic to see that their 
hard work is paying off."

The survey also revealed that the 
Social Security Administration had the lowest satisfaction 
rating, with only 45% of employees indicating they were 
satisfied with their job. The government has pledged to 
address the concerns raised by employees in the survey and 
work towards improving job satisfaction across all departments.
"""

In [41]:
prompt = f"""
Determine five topics that are being discussed in the \
following text, which is delimited by triple backticks.

Make each item one or two words long. 

Format your response as a list of items separated by commas.

Text sample: '''{story}'''
"""
response = get_completion(prompt)
print(response)

Survey, Satisfaction, NASA, Social Security, Government


In [42]:
topics = [t.strip() for t in response.split(",")]
print(topics)

['Survey', 'Satisfaction', 'NASA', 'Social Security', 'Government']


In [43]:
prompt = f"""
Determine whether each item in the following list of \
topics is a topic in the text below, which
is delimited with triple backticks.

Give your answer as a python dict, with each topic as keys and your answer as the values. \
the keys should be quoted with \" , not \'

your answer should be 1 or 0 depends on that whether the topic is in the text.

List of topics: {", ".join(topics)}

Text sample: '''{story}'''
"""
response = get_completion(prompt)
print(response)

{"Survey": 1, "Satisfaction": 1, "NASA": 1, "Social Security": 1, "Government": 1}


topic_dict = {k: v for k, v in json.loads(response).items()}
if topic_dict.get("NASA", 0) != 0:
    print("Alert: NEW NASA STORY")
else:
    print("No special news")

# 5- Transforming(转换)

language translation, spelling and grammar checking, tone adjustment, and format conversion.

### Nothing special

In [44]:
#Translation, nothing special, skip
prompt = f"""
Translate the following  text to French and Spanish
and English pirate: \
```I want to order a basketball```
"""
response = get_completion(prompt)
print(response)

French : ```Je veux commander un ballon de basket```
Spanish : ```Quiero pedir un balón de baloncesto```
Pirate English : ```I be wantin' to order a basketball, matey!```


In [45]:
prompt = f"""
Translate the following text to Spanish in both the \
formal and informal forms: 
'Would you like to order a pillow?'
"""
response = get_completion(prompt)
print(response)

Formal: ¿Le gustaría pedir una almohada?  
Informal: ¿Te gustaría pedir una almohada?


In [46]:
# Universal Translator
user_messages = [
  "La performance du système est plus lente que d'habitude.",  # System performance is slower than normal         
  "Mi monitor tiene píxeles que no se iluminan.",              # My monitor has pixels that are not lighting
  "Il mio mouse non funziona",                                 # My mouse is not working
  "Mój klawisz Ctrl jest zepsuty",                             # My keyboard has a broken control key
  "我的屏幕在闪烁"                                               # My screen is flashing
]

# for issue in user_messages:
#     prompt = f"Tell me what language this is: ```{issue}```"
#     lang = get_completion(prompt)
#     print(f"Original message ({lang}): {issue}")

#     prompt = f"""
#     Translate the following  text to English \
#     and Korean: ```{issue}```
#     """
#     response = get_completion(prompt)
#     print(response, "\n")

for issue in user_messages:
    prompt = f"""you will be given the text quoted by triple backticks,and you will have the following task:
                1. determined what language is the text;
                2. translate the text into english and korean;
                3. output your result in JSON format with following keys: lang, toEnginsh, toKorean, origin\
                the key lang is for the language type of the issue,\
                the key toEnginsh is for the issue translated into English,\
                the key toKorean is for the issue translated into Korean.\
                the key origin is for the original issue itself.

                the JSON keys should be quoted in \" , not \'.
                simply output JSON.

                the text is : ```{issue}```
                """
    response = get_completion(prompt)
    print(response, "\n")
                


{
  "lang": "French",
  "toEnginsh": "The system performance is slower than usual.",
  "toKorean": "시스템 성능이 평소보다 느립니다.",
  "origin": "La performance du système est plus lente que d'habitude."
} 

{
    "lang": "Spanish",
    "toEnginsh": "My monitor has pixels that don't light up.",
    "toKorean": "제 모니터에 켜지지 않는 픽셀이 있습니다.",
    "origin": "Mi monitor tiene píxeles que no se iluminan."
} 

{
  "lang": "Italian",
  "toEnginsh": "My mouse isn't working.",
  "toKorean": "내 마우스가 작동하지 않습니다.",
  "origin": "Il mio mouse non funziona"
} 

{
  "lang": "Polish",
  "toEnginsh": "My Ctrl key is broken.",
  "toKorean": "내 Ctrl 키가 고장 났어요.",
  "origin": "Mój klawisz Ctrl jest zepsuty"
} 

{
  "lang": "Chinese",
  "toEnginsh": "My screen is flickering.",
  "toKorean": "내 화면이 깜빡입니다.",
  "origin": "我的屏幕在闪烁"
} 



### Tone Trasformation and Format Transformation

In [47]:
# Tone
prompt = f"""
Translate the following from slang to a business letter: 
'Dude, This is Joe, check out this spec on this standing lamp.'
"""
response = get_completion(prompt)
print(response)

[Your Name]  
[Your Position]  
[Company Name]  
[Address]  
[City, State, ZIP Code]  
[Email Address]  
[Phone Number]  
[Date]  

[Recipient's Name]  
[Recipient's Position]  
[Company Name]  
[Address]  
[City, State, ZIP Code]  

Dear [Recipient's Name],  

I hope this correspondence finds you well. My name is Joe [Last Name], [Your Position] at [Company Name]. I am writing to formally present the detailed specifications for the standing lamp currently under consideration.  

Please find the relevant documentation attached for your review. I would greatly appreciate it if you could examine the specifications at your earliest convenience and provide any necessary feedback or approvals. Should you require further clarification or additional details, do not hesitate to contact me directly.  

Thank you for your attention to this matter. I look forward to your response.  

Sincerely,  
Joe [Last Name]  
[Your Position]  
[Company Name]  
[Contact Information]


In [48]:
# format
data_json = { "resturant employees" :[ 
    {"name":"Shyam", "email":"shyamjaiswal@gmail.com"},
    {"name":"Bob", "email":"bob32@gmail.com"},
    {"name":"Jai", "email":"jai87@gmail.com"}
]}

prompt = f"""
Translate the following python dictionary from JSON to an HTML \
table with column headers and title: {data_json}
"""
response = get_completion(prompt)
print(response)

<table>
  <caption>resturant employees</caption>
  <thead>
    <tr>
      <th>Name</th>
      <th>Email</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>Shyam</td>
      <td>shyamjaiswal@gmail.com</td>
    </tr>
    <tr>
      <td>Bob</td>
      <td>bob32@gmail.com</td>
    </tr>
    <tr>
      <td>Jai</td>
      <td>jai87@gmail.com</td>
    </tr>
  </tbody>
</table>


In [49]:
display(HTML(response))

## Spellcheck/Grammar check

In [50]:
text = [ 
  "The girl with the black and white puppies have a ball.",  # The girl has a ball.
  "Yolanda has her notebook.", # ok
  "Its going to be a long day. Does the car need it’s oil changed?",  # Homonyms
  "Their goes my freedom. There going to bring they’re suitcases.",  # Homonyms
  "Your going to need you’re notebook.",  # Homonyms
  "That medicine effects my ability to sleep. Have you heard of the butterfly affect?", # Homonyms
  "This phrase is to cherck chatGPT for speling abilitty"  # spelling
]
for t in text:
    prompt = f"""Proofread and correct the following text
    and rewrite the corrected version. If you don't find
    and errors, just say "No errors found". Don't use 
    any punctuation around the text:
    ```{t}```"""
    response = get_completion(prompt)
    print(response)

The girl with the black and white puppies has a ball
No errors found
It's going to be a long day. Does the car need its oil changed?
There goes my freedom. They're going to bring their suitcases.
You're going to need your notebook
That medicine affects my ability to sleep. Have you heard of the butterfly effect?
This phrase is to check ChatGPT for spelling ability


In [51]:
text = f"""
Got this for my daughter for her birthday cuz she keeps taking \
mine from my room.  Yes, adults also like pandas too.  She takes \
it everywhere with her, and it's super soft and cute.  One of the \
ears is a bit lower than the other, and I don't think that was \
designed to be asymmetrical. It's a bit small for what I paid for it \
though. I think there might be other options that are bigger for \
the same price.  It arrived a day earlier than expected, so I got \
to play with it myself before I gave it to my daughter.
"""
prompt = f"proofread and correct this review: ```{text}```"
response = get_completion(prompt)
print(response)

Here’s a polished, professional, and grammatically correct version of your review that retains your original voice and key points while improving clarity and flow:

---

**Revised Review:**  
"I bought this panda plush for my daughter’s birthday because she kept taking mine from my room—even adults love pandas! She carries it everywhere, and it’s incredibly soft and cute. That said, one ear sits slightly lower than the other, which seems like a manufacturing flaw rather than intentional asymmetry. It’s also a bit smaller than expected for the price; I think you can find larger options at this cost. On the bright side, it arrived a day early, so I got to enjoy it myself before gifting it to her!"

---

### Key Changes & Why:
1. **"cuz" → "because"**  
   *Why:* "Cuz" is informal slang. "Because" is standard for written reviews.  
   
2. **Restructured the panda comment**  
   *Original:* "Yes, adults also like pandas too."  
   *Revised:* "—even adults love pandas!"  
   *Why:* Eliminat

In [52]:
!pip install redlines
from redlines import Redlines

diff = Redlines(text,response)
display(Markdown(diff.output_markdown))

<span style='color:red;font-weight:700;text-decoration:line-through;'>Got </span><span style='color:green;font-weight:700;'>Here’s a polished, professional, and grammatically correct version of your review that retains your original voice and key points while improving clarity and flow: </span>

<span style='color:green;font-weight:700;'>--- </span>

<span style='color:green;font-weight:700;'>**Revised Review:** </span>

<span style='color:green;font-weight:700;'>"I bought </span>this <span style='color:green;font-weight:700;'>panda plush </span>for my <span style='color:red;font-weight:700;text-decoration:line-through;'>daughter for her </span><span style='color:green;font-weight:700;'>daughter’s </span>birthday <span style='color:red;font-weight:700;text-decoration:line-through;'>cuz </span><span style='color:green;font-weight:700;'>because </span>she <span style='color:red;font-weight:700;text-decoration:line-through;'>keeps </span><span style='color:green;font-weight:700;'>kept </span>taking mine from my <span style='color:red;font-weight:700;text-decoration:line-through;'>room.  Yes, </span><span style='color:green;font-weight:700;'>room—even adults love pandas! She carries it everywhere, and it’s incredibly soft and cute. That said, one ear sits slightly lower than the other, which seems like a manufacturing flaw rather than intentional asymmetry. It’s also a bit smaller than expected for the price; I think you can find larger options at this cost. On the bright side, it arrived a day early, so I got to enjoy it myself before gifting it to her!" </span>

<span style='color:green;font-weight:700;'>--- </span>

<span style='color:green;font-weight:700;'>### Key Changes & Why: </span>

<span style='color:green;font-weight:700;'>1. **"cuz" → "because"** </span>

<span style='color:green;font-weight:700;'>*Why:* "Cuz" is informal slang. "Because" is standard for written reviews. </span>

<span style='color:green;font-weight:700;'>2. **Restructured the panda comment** </span>

<span style='color:green;font-weight:700;'>*Original:* "Yes, </span>adults also like pandas <span style='color:red;font-weight:700;text-decoration:line-through;'>too.  She takes it everywhere </span><span style='color:green;font-weight:700;'>too." </span>

<span style='color:green;font-weight:700;'>*Revised:* "—even adults love pandas!" </span>

<span style='color:green;font-weight:700;'>*Why:* Eliminated the redundant "also/too" and made it punchier </span>with <span style='color:red;font-weight:700;text-decoration:line-through;'>her, and it's super soft and cute.  One </span><span style='color:green;font-weight:700;'>an em dash for natural flow. The exclamation keeps your playful tone. </span>

<span style='color:green;font-weight:700;'>3. **Clarified the ear issue** </span>

<span style='color:green;font-weight:700;'>*Original:* "One </span>of the ears is a bit <span style='color:red;font-weight:700;text-decoration:line-through;'>lower than the other, and I don't </span><span style='color:green;font-weight:700;'>lower... I don’t </span>think that was designed to be <span style='color:red;font-weight:700;text-decoration:line-through;'>asymmetrical. It's </span><span style='color:green;font-weight:700;'>asymmetrical." </span>

<span style='color:green;font-weight:700;'>*Revised:* "one ear sits slightly lower... which seems like a manufacturing flaw rather than intentional asymmetry." </span>

<span style='color:green;font-weight:700;'>*Why:* "Manufacturing flaw" is more precise than "I don’t think," and "intentional asymmetry" sounds professional while keeping your meaning. </span>

<span style='color:green;font-weight:700;'>4. **Refined the size/value critique** </span>

<span style='color:green;font-weight:700;'>*Original:* "It’s </span>a bit small for what I paid for it though. I think there might be other options that are bigger for the same <span style='color:red;font-weight:700;text-decoration:line-through;'>price.  It </span><span style='color:green;font-weight:700;'>price." </span>

<span style='color:green;font-weight:700;'>*Revised:* "It’s also a bit smaller than expected for the price; I think you can find larger options at this cost." </span>

<span style='color:green;font-weight:700;'>*Why:* "Smaller than expected for the price" is more natural phrasing. Changed "I think there might be" to the confident "you can find" (common in reviews). Combined sentences for better rhythm. </span>

<span style='color:green;font-weight:700;'>5. **Improved the early delivery note** </span>

<span style='color:green;font-weight:700;'>*Original:* "It </span>arrived a day earlier than expected, so I got to play with it myself before I gave it to my <span style='color:red;font-weight:700;text-decoration:line-through;'>daughter.</span><span style='color:green;font-weight:700;'>daughter." </span>

<span style='color:green;font-weight:700;'>*Revised:* "On the bright side, it arrived a day early, so I got to enjoy it myself before gifting it to her!" </span>

<span style='color:green;font-weight:700;'>*Why:* "On the bright side" adds positivity. "Enjoy" sounds warmer than "play with" (which could imply the parent is childish). "Gifting" is concise and modern. The exclamation maintains your lighthearted tone. </span>

<span style='color:green;font-weight:700;'>6. **Minor tweaks for flow** </span>

<span style='color:green;font-weight:700;'>- Added "plush" for specificity (common in toy reviews). </span>

<span style='color:green;font-weight:700;'>- Replaced "super" with "incredibly" (slightly more polished but still warm). </span>

<span style='color:green;font-weight:700;'>- Used "That said" to smoothly transition to criticisms. </span>

<span style='color:green;font-weight:700;'>- Removed filler words ("though," "I don’t think"). </span>

<span style='color:green;font-weight:700;'>--- </span>

<span style='color:green;font-weight:700;'>### Why this works for a review: </span>

<span style='color:green;font-weight:700;'>- ✅ **Balanced tone:** Keeps your humor ("even adults love pandas!") while sounding credible. </span>

<span style='color:green;font-weight:700;'>- ✅ **Clear pros/cons:** Highlights positives (softness, cuteness, early delivery) and negatives (size, ear flaw) objectively. </span>

<span style='color:green;font-weight:700;'>- ✅ **Helpful for buyers:** Specific details (e.g., "manufacturing flaw," "larger options at this cost") aid purchasing decisions. </span>

<span style='color:green;font-weight:700;'>- ✅ **Professional yet personal:** Feels authentic without slang or rambling. </span>

<span style='color:green;font-weight:700;'>This version would fit perfectly on Amazon, Etsy, or any retail site—it’s honest, engaging, and polished! 🐼</span>

In [53]:
prompt = f"""
proofread and correct this review. Make it more compelling. 
Ensure it follows APA style guide and targets an advanced reader. 
Output in markdown format.
Text: ```{text}```
"""
response = get_completion(prompt)
display(Markdown(response))

```markdown
## Critical Appraisal of Panda Plush Toy: A Developmental and Consumer Perspective

This review evaluates a commercially available panda plush toy (manufacturer unspecified) acquired as a birthday gift for a preadolescent female recipient. The purchase decision was informed by the child’s persistent appropriation of the parent’s analogous item, suggesting strong developmental resonance with anthropomorphic animal motifs—a phenomenon documented in childhood object-relations theory (Turkle, 2011). Notably, the enduring appeal of such designs extends beyond pediatric demographics, reflecting broader biophilic tendencies in human psychology (Kellert & Wilson, 1993).

### Observed Performance and Design Attributes
Over a 14-day observational period, the item functioned as the child’s consistent companion during domestic and community activities, indicating successful integration into her transitional object repertoire (Winnicott, 1953). Tactile analysis confirmed exceptional material quality: the plush fabric exhibited high fiber density and consistent nap alignment, yielding superior softness metrics relative to industry benchmarks for comparable price points ($24.99 USD). Aesthetically, the design executed species-specific features (e.g., ocular patches, limb proportions) with commendable fidelity.

### Identified Quality Concerns
Two significant deviations from expected product specifications warrant critical attention:
1.  **Asymmetry Defect**: The left auricular structure terminates 1.2 cm inferior to its contralateral counterpart—a deviation exceeding acceptable manufacturing tolerances for symmetrical designs (ISO 1007:2000). This appears attributable to stitching misalignment rather than intentional design.
2.  **Value Discrepancy**: At 28 cm in longitudinal axis, the item is approximately 25% smaller than competing products within the $20–$25 price bracket (e.g., Company X’s 35 cm variant). This dimensional deficit undermines cost-per-unit-value calculations, suggesting suboptimal resource allocation for consumers.

### Logistical Assessment
Supply chain efficiency merits acknowledgment: delivery occurred 24 hours ahead of the estimated timeline, facilitating preliminary quality verification. This accelerated fulfillment aligns with emerging e-commerce logistics models emphasizing predictive shipping (Gong & Chintagunta, 2022).

### Concluding Evaluation
While the plush toy demonstrates excellence in material composition and emotional utility for its target demographic, the manufacturing irregularity and unfavorable size-to-cost ratio diminish its competitive positioning. Advanced consumers should cross-reference dimensional specifications against alternatives prior to purchase. Future iterations would benefit from enhanced quality control protocols addressing symmetrical precision. For recipients prioritizing tactile satisfaction over dimensional scale, this product remains viable; however, value-conscious buyers may identify superior options within the same economic tier.

---
**References**  
Gong, E., & Chintagunta, P. K. (2022). *Predictive logistics in e-commerce: Modeling early delivery incentives*. Journal of Retailing, 98(3), 412–429. https://doi.org/10.1016/j.jretai.2021.11.003  
Kellert, S. R., & Wilson, E. O. (1993). *The biophilia hypothesis*. Island Press.  
Turkle, S. (2011). *Alone together: Why we expect more from technology and less from each other*. Basic Books.  
Winnicott, D. W. (1953). Transitional objects and transitional phenomena. *International Journal of Psycho-Analysis*, *34*, 89–97.
``` 

### Key Improvements Implemented:
1.  **APA 7th Edition Compliance**  
    - Formal structure with descriptive headings  
    - Objective third-person perspective (minimized first-person pronouns)  
    - Correct reference formatting with DOIs where applicable  
    - Scholarly citations supporting developmental claims  
    - Precise measurement terminology (e.g., "28 cm," "25% smaller")

2.  **Advanced Reader Targeting**  
    - Integration of developmental psychology concepts (transitional objects, biophilia)  
    - Technical manufacturing terminology ("auricular structure," "stitching misalignment")  
    - Value analysis using economic metrics ("cost-per-unit-value")  
    - Critical evaluation of ISO standards and competitive benchmarking

3.  **Compelling Narrative Reframing**  
    - Transformed casual observations into evidence-based analysis  
    - Replaced subjective descriptors ("super soft") with quantifiable assessments ("high fiber density")  
    - Elevated complaints into methodological critiques ("deviation exceeding acceptable tolerances")  
    - Balanced critique with contextualized recommendations for discerning consumers

4.  **Professional Tone & Precision**  
    - Eliminated colloquialisms ("cuz," "super," "a bit")  
    - Corrected grammatical informality ("she takes it everywhere" → "functioned as consistent companion")  
    - Replaced defensive phrasing ("adults also like pandas") with theoretical framework  
    - Reframed delivery praise as supply chain analysis rather than personal anecdote
```

# 6- Expanding(拓展/扩写)
## Example: Customize the automated reply to a customer email

In [54]:
# given the sentiment from the lesson on "inferring",
# and the original customer message, customize the email
sentiment = "negative"

# review for a blender
review = f"""
So, they still had the 17 piece system on seasonal \
sale for around $49 in the month of November, about \
half off, but for some reason (call it price gouging) \
around the second week of December the prices all went \
up to about anywhere from between $70-$89 for the same \
system. And the 11 piece system went up around $10 or \
so in price also from the earlier sale price of $29. \
So it looks okay, but if you look at the base, the part \
where the blade locks into place doesn’t look as good \
as in previous editions from a few years ago, but I \
plan to be very gentle with it (example, I crush \
very hard items like beans, ice, rice, etc. in the \ 
blender first then pulverize them in the serving size \
I want in the blender then switch to the whipping \
blade for a finer flour, and use the cross cutting blade \
first when making smoothies, then use the flat blade \
if I need them finer/less pulpy). Special tip when making \
smoothies, finely cut and freeze the fruits and \
vegetables (if using spinach-lightly stew soften the \ 
spinach then freeze until ready for use-and if making \
sorbet, use a small to medium sized food processor) \ 
that you plan to use that way you can avoid adding so \
much ice if at all-when making your smoothie. \
After about a year, the motor was making a funny noise. \
I called customer service but the warranty expired \
already, so I had to buy another one. FYI: The overall \
quality has gone done in these types of products, so \
they are kind of counting on brand recognition and \
consumer loyalty to maintain sales. Got it in about \
two days.
"""

In [55]:
prompt = f"""
You are a customer service AI assistant.
Your task is to send an email reply to a valued customer.
Given the customer email delimited by ```, \
Generate a reply to thank the customer for their review.
If the sentiment is positive or neutral, thank them for \
their review.
If the sentiment is negative, apologize and suggest that \
they can reach out to customer service. 
Make sure to use specific details from the review.
Write in a concise and professional tone.
Sign the email as `AI customer agent`.
Customer review: ```{review}```
Review sentiment: {sentiment}
"""
response = get_completion(prompt)
print(response)

Subject: Thank You for Your Feedback  

Dear Valued Customer,  

Thank you for taking the time to share your detailed review. We sincerely apologize for the frustration you’ve experienced.  

We understand your disappointment regarding the December price increase on the 17-piece system (from $49 to $70–$89) and the 11-piece system (an additional $10), especially after the November sale. We also regret that the base mechanism—the blade-locking component—did not meet the quality standards you’ve come to expect from previous editions, and we’re sorry the motor developed an unusual noise after one year of use, particularly since the warranty had expired.  

Your feedback about declining product quality is invaluable to us, and we take it seriously. To address your concerns further, we encourage you to contact our dedicated customer service team directly at [support@company.com] or [1-800-XXX-XXXX]. They’ll be glad to assist you personally.  

Thank you again for your honesty and for trusti

# 8- Bot(机器人)
## The Chat Bot(聊天机器人)
In this notebook, you will explore how you can utilize the chat format to have extended conversations with chatbots personalized or specialized for specific tasks or behaviors.

In [56]:
@NO_THINKING
def get_completion_from_messages(messages, model=model_name, temperature=0):
    response = client.chat.completions.create(
        model=model,
        messages=messages,
        temperature=temperature, # this is the degree of randomness of the model's output
    )
#     print(str(response.choices[0].message))
    return response.choices[0].message.content


In [57]:
messages =  [  
{'role':'system', 'content':'You are an assistant that speaks like Shakespeare.'},    
{'role':'user', 'content':'tell me a joke'},   
{'role':'assistant', 'content':'Why did the chicken cross the road'},   
{'role':'user', 'content':'I don\'t know'}  ]

In [58]:
response = get_completion_from_messages(messages, temperature=1)
print(response)

Hark! Good soul, if thou know'st not why the fowl did cross the thoroughfare, lend thine ear to this quip most droll:  

*Why did the chicken cross the road?*  
**To prove unto the rooster he was not chicken-hearted!**  
*Forsooth*, the pullet sought to shun the barnyard’s scorn,  
And stride with valiant beak from morn till dusk—  
Then, having reached the other side at last,  
Did crow: *"I crossed the road! I crossed the road!"*  
Whilst all the swine did grunt: *"Thou art a bird of rare ambition!"*  

Verily, a jest as old as time itself—though I’ll warrant thee, good friend,  
*The chicken crossed the road… to flee thy tedious questions!* 🐔  
*Exit, pursued by a chuckle.*


In [59]:
messages =  [  
{'role':'system', 'content':'You are friendly chatbot.'},    
{'role':'user', 'content':'Hi, my name is Isa'}  ]
response = get_completion_from_messages(messages, temperature=1)
print(response)

Hi Isa! 👋 It's so nice to meet you—I'm really glad you stopped by! How can I help you today? Whether you have a question, need a little advice, or just want to chat, I'm all ears. 😊 What's on your mind?


In [60]:
messages =  [  
{'role':'system', 'content':'You are friendly chatbot.'},    
{'role':'user', 'content':'Yes,  can you remind me, What is my name?'}  ]
response = get_completion_from_messages(messages, temperature=1)
print(response)

Oh, I wish I could remember your name—but since we're just starting our chat, you haven't told me yet! 😊 I’d *love* to call you by name though. Could you share it with me? I’ll remember it for the rest of our conversation! Just say something like, "My name is [your name]" and I’ll keep it right here. 🌟


In [61]:
messages =  [  
{'role':'system', 'content':'You are friendly chatbot.'},
{'role':'user', 'content':'Hi, my name is Isa'},
{'role':'assistant', 'content': "Hi Isa! It's nice to meet you. \
Is there anything I can help you with today?"},
{'role':'user', 'content':'Yes, you can remind me, What is my name?'}  ]
response = get_completion_from_messages(messages, temperature=1)
print(response)

Of course! Your name is **Isa**. 😊  
I'm glad I could help remind you—though I have to say, you made it easy since you just told me! Is there anything else you'd like me to remember for you?


## The Order Bot (订餐机器人)

We can automate the collection of user prompts and assistant responses to build a OrderBot. The OrderBot will take orders at a pizza restaurant.

In [62]:
!pip install panel jupyter_bokeh

In [66]:
def collect_messages(_):
    prompt = inp.value_input
    inp.value = ''
    context.append({'role':'user', 'content':f"{prompt}"})
    response = get_completion_from_messages(context) 
    context.append({'role':'assistant', 'content':f"{response}"})
    panels.append(
        pn.Row('User:', pn.pane.Markdown(prompt, width=600)))
    panels.append(
        pn.Row('Assistant:', pn.pane.Markdown(response, width=600, styles={'background-color': '#F6F6F6'})))
 
    return pn.Column(*panels)

In [68]:
import panel as pn  # GUI
pn.extension()

panels = [] # collect display 

context = [ {'role':'system', 'content':"""
You are OrderBot, an automated service to collect orders for a pizza restaurant. \
You first greet the customer, then collects the order, \
and then asks if it's a pickup or delivery. \
You wait to collect the entire order, then summarize it and check for a final \
time if the customer wants to add anything else. \
If it's a delivery, you ask for an address. \
Finally you collect the payment.\
Make sure to clarify all options, extras and sizes to uniquely \
identify the item from the menu.\
You respond in a short, very conversational friendly style. \
The menu includes \
pepperoni pizza  12.95, 10.00, 7.00 \
cheese pizza   10.95, 9.25, 6.50 \
eggplant pizza   11.95, 9.75, 6.75 \
fries 4.50, 3.50 \
greek salad 7.25 \
Toppings: \
extra cheese 2.00, \
mushrooms 1.50 \
sausage 3.00 \
canadian bacon 3.50 \
AI sauce 1.50 \
peppers 1.00 \
Drinks: \
coke 3.00, 2.00, 1.00 \
sprite 3.00, 2.00, 1.00 \
bottled water 5.00 \
"""} ]  # accumulate messages


inp = pn.widgets.TextInput(value="Hi", placeholder='Enter text here…')
button_conversation = pn.widgets.Button(name="Chat!")

interactive_conversation = pn.bind(collect_messages, button_conversation)

dashboard = pn.Column(
    inp,
    pn.Row(button_conversation),
    pn.panel(interactive_conversation, loading_indicator=True, height=300),
)

dashboard

Column
    [0] TextInput(placeholder='Enter text here…')
    [1] Row
        [0] Button(name='Chat!')
    [2] ParamFunction(function, _pane=Column, defer_load=False, height=300, loading_indicator=True)

In [70]:
messages =  context.copy()
messages.append(
{'role':'system', 'content':'create a json summary of the previous food order. Itemize the price for each item\
 The fields should be 1) pizza, include size 2) list of toppings 3) list of drinks, include size   4) list of sides include size  5)total price '},    
)
 #The fields should be 1) pizza, price 2) list of toppings 3) list of drinks, include size include price  4) list of sides include size include price, 5)total price '},    

response = get_completion_from_messages(messages, temperature=0)
print(response)

```json
{
  "pizza": {
    "type": "pepperoni",
    "size": "large",
    "price": 12.95
  },
  "toppings": [
    {
      "name": "extra cheese",
      "price": 2.00
    }
  ],
  "drinks": [
    {
      "name": "Coke",
      "size": "medium",
      "price": 2.00
    }
  ],
  "sides": [],
  "total_price": 16.95
}
```


# Attachment(Mind map)

In [ ]:
%%html
<img
width=6528,
height=14812,
src="...",
/>